In [ ]:
import pandas as pd
import numpy as np
import pandera.pandas as pa 

import re
import ast




In [119]:
# Load your data
bios_df = pd.read_csv("../clean_data/cleaned_biodata.csv")
results_df = pd.read_csv('../clean_data/cleaned_results.csv')

affiliation_df = pd.read_csv("../clean_data/dim_affiliation.csv")

In [ ]:
bios_df

In [ ]:
bios_df.info()

In [ ]:
bios_df.describe(include='all')

In [39]:
def df_nan_percentage(df):
    return df.isna().mean().mul(100).round(2).sort_values(ascending=False).map(lambda x: f"{x}%")
df_nan_percentage(affiliation_df)

Affiliation_Country    51.87%
Affiliation_City        48.0%
Affiliation_Club        0.01%
Affiliation_Id           0.0%
dtype: object

In [118]:
affiliation_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 38830 entries, 0 to 38829
Data columns (total 4 columns):
 #   Column               Non-Null Count  Dtype 
---  ------               --------------  ----- 
 0   Affiliation_Id       38830 non-null  int64 
 1   Affiliation_Club     38828 non-null  object
 2   Affiliation_City     20190 non-null  object
 3   Affiliation_Country  18688 non-null  object
dtypes: int64(1), object(3)
memory usage: 1.2+ MB


In [ ]:
df_nan_percentage(affiliation_df)

In [ ]:
# Count how many disciplines per athlete
discipline_counts = results_df.groupby('Athlete_Id')['Discipline'].nunique()

# See if any have more than 1
multi_discipline = discipline_counts[discipline_counts > 1]

print(f"Number of athletes with multiple disciplines: {len(multi_discipline)}")
print(f"Total athletes in results: {len(discipline_counts)}")
print(f"Percentage: {len(multi_discipline) / len(discipline_counts) * 100:.2f}%")

In [ ]:
print("Duplicate Athlete_Id in bio_df:", bios_df['Athlete_Id'].duplicated().sum())
print("Total rows in bio_df:", len(bios_df))
print("Unique Athlete_Id:", bios_df['Athlete_Id'].nunique())

In [ ]:
def impute_height_weight_by_discipline(bio_df, results_df):
    """
    Impute Height (cm) and Weight (kg) using the median of
    Sex + Discipline (primary) and Sex only (fallback).

    Parameters
    ----------
    bio_df      : DataFrame with columns ['Athlete_Id', 'Sex', 'Height (cm)', 'Weight (kg)', ...]
    results_df  : DataFrame with columns ['Athlete_Id', 'Discipline', ...]

    Returns
    -------
    bio_imputed : DataFrame (same shape as bio_df) with imputed values and two flag columns
    """
    bio = bio_df.copy()

    # -------------------------------------------------
    # 1. ONE DISCIPLINE PER ATHLETE (most frequent)
    # -------------------------------------------------
    discipline_map = (
        results_df.groupby('Athlete_Id')['Discipline']
        .apply(lambda s: s.mode().iloc[0] if not s.mode().empty else np.nan)
        .reset_index()
    )
    bio = bio.merge(discipline_map, on='Athlete_Id', how='left')

    # -------------------------------------------------
    # 2. IMPUTATION FLAGS (before any filling)
    # -------------------------------------------------
    bio['Height_Imputed'] = bio['Height (cm)'].isna()
    bio['Weight_Imputed'] = bio['Weight (kg)'].isna()

    # -------------------------------------------------
    # 3. MEDIANS BY Sex + Discipline
    # -------------------------------------------------
    grp = bio.groupby(['Sex', 'Discipline'])
    height_med_sex_disc = grp['Height (cm)'].transform('median')
    weight_med_sex_disc = grp['Weight (kg)'].transform('median')

    # Fill with Sex+Discipline median where possible
    bio['Height (cm)'] = bio['Height (cm)'].fillna(height_med_sex_disc)
    bio['Weight (kg)'] = bio['Weight (kg)'].fillna(weight_med_sex_disc)

    # -------------------------------------------------
    # 4. FALLBACK: MEDIAN BY Sex ONLY
    # -------------------------------------------------
    bio['Height (cm)'] = bio.groupby('Sex')['Height (cm)'].transform(
        lambda x: x.fillna(x.median())
    )
    bio['Weight (kg)'] = bio.groupby('Sex')['Weight (kg)'].transform(
        lambda x: x.fillna(x.median())
    )

    # -------------------------------------------------
    # 5. UPDATE FLAGS FOR FALLBACK IMPUTATIONS
    # -------------------------------------------------
    # Original missing values that are now filled
    orig_height_na = bio_df['Height (cm)'].isna()
    orig_weight_na = bio_df['Weight (kg)'].isna()

    bio['Height_Imputed'] = bio['Height_Imputed'] | (orig_height_na & bio['Height (cm)'].notna())
    bio['Weight_Imputed'] = bio['Weight_Imputed'] | (orig_weight_na & bio['Weight (kg)'].notna())

    # -------------------------------------------------
    # 6. CLEAN-UP
    # -------------------------------------------------
    bio = bio.drop(columns=['Discipline'])

    return bio

In [ ]:


# Impute!
bios_df = impute_height_weight_by_discipline(bios_df, results_df)



In [ ]:
bios_df.isna().mean().mul(100).round(2).sort_values(ascending=False).map(lambda x: f"{x}%")

In [ ]:
def impute_Born_Country_by_NOC(bios_df):
    # clean_bio_df = pd.read_csv('your_bio_df.csv')  # assuming it's already loaded
    bios_df = bios_df.copy()
    # Load the ISO country codes CSV
    iso_df = pd.read_csv('../data/wikipedia-iso-country-codes.csv')

    # Create a mapping from lowercase English short name to Alpha-3 code
    country_to_code = dict(zip(iso_df['English short name lower case'].str.lower(), iso_df['Alpha-3 code']))

    # Function to get the first NOC country code
    def get_noc_code(noc_list):
        noc_list = ast.literal_eval(noc_list)
        if len(noc_list) > 0:
            return country_to_code.get(noc_list[0])
        return np.nan

    # Create a flag column to indicate when Born_Country is derived from NOC
    bios_df['Born_Country_From_NOC'] = False

    # Apply the function only where Born_Country is missing
    mask = bios_df['Born_Country'].isna()
    bios_df.loc[mask, 'Born_Country'] = bios_df.loc[mask, 'NOC'].apply(get_noc_code)
    bios_df.loc[mask, 'Born_Country_From_NOC'] = True
    
    return bios_df

In [ ]:
bios_df = impute_Born_Country_by_NOC(bios_df)

In [ ]:
bios_df

country_to_code = dict(zip(iso_df['English short name lower case'].str.lower(), iso_df['Alpha-3 code']))
country_to_code.get('france')


In [ ]:
count_none = len(bios_df[(bios_df['Born_Country_From_NOC']==True) & (bios_df['Born_Country'].isna())])
count_not_none = len(bios_df[(bios_df['Born_Country_From_NOC']==True) & (bios_df['Born_Country'].notna())])

print(f"Count of None in Born_Country where derived from NOC: {count_none}")
print(f"Count of Not None in Born_Country where derived from NOC: {count_not_none}")

In [ ]:
bios_df.isna().mean().mul(100).round(2).sort_values(ascending=False).map(lambda x: f"{x}%")

In [ ]:
# bios_df[bios_df['Athlete_Id'].isin([1812, 3997, 6237, 6292, 6317, 6468, 6679, 6759, 6775, 6863, 7015, 7158, 7250, 7673, 8270, 8928, 11272, 11572, 11706, 11779, 12191, 13017, 15259, 17449, 17613, 17635, 19553, 19621, 19626, 20180, 21166, 21750, 22025, 22362, 22368, 23530, 23541, 24096, 24429, 24722, 24749, 24755, 24779, 24787, 24790, 24809, 24817, 25804, 26222, 28041, 30715, 31008, 31912, 38083, 39441, 39442, 39444, 39452, 39457, 39798, 39814, 40973, 40972, 41015, 41298, 42210, 42240, 42660, 46418, 47918, 47978, 50179, 53725, 54682, 54710, 55563, 58663, 58795, 58818, 58907, 60619, 61190, 68201, 72894, 79628, 79765, 79824, 79881, 79900, 79957, 128839])]
bios_df[bios_df['Name'].isin(['Ahmed Salem', 'Nikolaos Kaloudis', 'Georges Dubois'])]



In [ ]:

# Exact duplicates
dupes = bios_df[bios_df.duplicated()]
print(f"Exact duplicates: {len(dupes)}")

# Potential duplicates (same Name + Born_Date or Athlete_Id)
possible_dupes = bios_df[bios_df.duplicated(subset=['Name', 'Born_Date'], keep=False)]
print(f"possible duplicates: {len(possible_dupes)}")


In [122]:
def is_list_of_strings(x):
    return all(isinstance(r, str) for r in x)

no_duplicate_name_birth = pa.Check(
    lambda df: ~df.duplicated(subset=["Name", "Born_Date"]),
    element_wise=False,
    error="Duplicate athlete records found with same Name and Born_Date."
)

date_logic = pa.Check(
    lambda df: (df["Born_Date"].isna() | df["Died_Date"].isna()) | (df["Died_Date"] >= df["Born_Date"]),
    element_wise=False,
    error="Died_Date earlier than Born_Date."
)


height_weight_logic = pa.Check(
    lambda df: (
        (df["Weight (kg)"] / ((df["Height (cm)"] / 100) ** 2)).between(15, 45)
    ),
    error="Unrealistic height-to-weight ratio."
)

In [ ]:


bio_schema = pa.DataFrameSchema(
    { 
        "Athlete_Id": pa.Column(int, pa.Check.ge(1), nullable=False, unique=True), 
        "Name": pa.Column(str, nullable=False), 
        "Sex": pa.Column(str, pa.Check.isin(["Male", "Female"]), nullable=False), 
        "NOC": pa.Column(str, pa.Check(is_list_of_strings, element_wise=False ), nullable=True),

        "Height (cm)": pa.Column(float, pa.Check.between(100,250), nullable=True), 
        "Weight (kg)": pa.Column(float, pa.Check.between(25,200), nullable=True), 
        "Height_Imputed": pa.Column(bool, nullable=False),
        "Weight_Imputed": pa.Column(bool, nullable=False),

        "Born_Date": pa.Column("datetime64[ns]", nullable=True), 
        "Died_Date": pa.Column("datetime64[ns]", nullable=True),
        'Is_Alive': pa.Column(bool, nullable=False),

        "Born_City": pa.Column(str, nullable=True), 
        "Born_Region": pa.Column(str, nullable=True), 
        "Born_Country": pa.Column(str, pa.Check.str_length(3, 3), nullable=True), 
        "Born_Country_From_NOC": pa.Column(bool, nullable=False),

        "Roles": pa.Column(object,pa.Check(is_list_of_strings, element_wise=False ), nullable=True) 
        
        }, 
        strict=True, 
        coerce=True,
        
        checks=[

            no_duplicate_name_birth,
            date_logic,
            height_weight_logic

            ]

        ) 



try: 
    bio_schema.validate(bios_df, lazy=True) 
    print("Validation PASSED!") 
    
except pa.errors.SchemaErrors as exc: 
    print("Validation FAILED!") 
    error_df = exc.failure_cases
    print(exc)

Validation FAILED!
{
    "SCHEMA": {
        "COLUMN_NOT_IN_SCHEMA": [
            {
                "schema": null,
                "column": null,
                "check": "column_in_schema",
                "error": "column 'Is_Alive' not in DataFrameSchema {'Athlete_Id': <Schema Column(name=Athlete_Id, type=DataType(int64))>, 'Name': <Schema Column(name=Name, type=DataType(str))>, 'Sex': <Schema Column(name=Sex, type=DataType(str))>, 'NOC': <Schema Column(name=NOC, type=DataType(str))>, 'Height (cm)': <Schema Column(name=Height (cm), type=DataType(float64))>, 'Weight (kg)': <Schema Column(name=Weight (kg), type=DataType(float64))>, 'Height_Imputed': <Schema Column(name=Height_Imputed, type=DataType(bool))>, 'Weight_Imputed': <Schema Column(name=Weight_Imputed, type=DataType(bool))>, 'Born_Date': <Schema Column(name=Born_Date, type=DataType(datetime64[ns]))>, 'Died_Date': <Schema Column(name=Died_Date, type=DataType(datetime64[ns]))>, 'Is_Deceased': <Schema Column(name=Is_Deceased, 

In [ ]:
error_df

In [ ]:
duplicate_affiliation_content_check = pa.Check(
    lambda df: not df.duplicated(subset=["Affiliation_Club", "Affiliation_City", "Affiliation_Country"]).any(),
    element_wise=False,
    error="Duplicate affiliations found with different Affiliation_Ids (same club, city, and country)."
)

affiliation_schema = pa.DataFrameSchema(
    { 
        "Affiliation_Id": pa.Column(int, pa.Check.ge(0), nullable=False, unique=True), 

        "Affiliation_Club": pa.Column(str, nullable=True), 
        "Affiliation_City": pa.Column(str, nullable=True), 
        "Affiliation_Country": pa.Column(str, pa.Check.str_length(3, 3), nullable=True), 

        }, 

        strict=True, 
        coerce=True,
        
        checks=[
            duplicate_affiliation_content_check
            ]
        ) 


try: 
    
    affiliation_schema.validate(affiliation_df, lazy=True) 
    print("Validation PASSED!") 
    
except pa.errors.SchemaErrors as exc: 
    print("Validation FAILED!") 
    error_df = exc.failure_cases
    print(exc)

In [ ]:
bios_df[bios_df['Height_Imputed']==True][['Height (cm)','Height_Imputed','Sex','Name']].sample(10)

In [ ]:
results_df.info()

In [ ]:
results_df

In [ ]:
df_nan_percentage(results_df)

In [ ]:
medal_position_logic_check = pa.Check(
    lambda df: (
        df["Medal"].isna() | (df["Position"] <= 3)
    ),
    error="Medal assigned to invalid position (must be ≤ 3)."
)
position_medal_match_check = pa.Check(
    lambda df: (
        df["Position"].isna()
        | (
            ((df["Position"] == 1) & (df["Medal"] == "Gold"))
            | ((df["Position"] == 2) & (df["Medal"] == "Silver"))
            | ((df["Position"] == 3) & (df["Medal"] == "Bronze"))
            | (df["Position"] > 3) & (df["Medal"].isna())
        )
    ),
    error="Position–Medal mismatch: check if medal corresponds to rank."
)


In [ ]:
# --- Schema Definition ---
fact_events_schema = pa.DataFrameSchema(
    {

        "Athlete_Id": pa.Column(int, pa.Check.ge(1), nullable=False),
        "As":   pa.Column(str, nullable=False),
        "NOC": pa.Column(str, pa.Check.str_length(3, 3), nullable=False),
        "Discipline": pa.Column(str, nullable=False),
        "Game Type": pa.Column(str, nullable=True),
        "Game Year": pa.Column(float, pa.Check.between(1850, 2024), nullable=True),


        "Event": pa.Column(str, nullable=True),
        "Team": pa.Column(str, nullable=True),
        "Tied": pa.Column(bool, nullable=True),


        "Position": pa.Column(float,pa.Check.ge(1), nullable=True),
        "Medal": pa.Column(
            str,
            pa.Check.isin(["Gold", "Silver", "Bronze"]),
            nullable=True
        ),

    },
    strict=True,
    coerce=True,
    checks=[
        medal_position_logic_check,
        position_medal_match_check

    ],

)

# --- Validation ---
try:
    fact_events_schema.validate(results_df, lazy=True)
    print("Validation PASSED!")
except pa.errors.SchemaErrors as exc:
    print("Validation FAILED!")
    error_df = exc.failure_cases
    print(exc)

In [ ]:
dim_affiliation_df = pd.read_csv("../clean_data/dim_affiliation.csv")
editions_df = pd.read_csv('../clean_data/cleaned_editions.csv')

In [ ]:
editions_df.info()

In [ ]:
# editions_df
df_nan_percentage(editions_df)

In [ ]:
def impute_games_and_competition_dates(df):
    df = df.copy()

    # Initialize flag columns as False (no imputation by default)
    df["Opened_Imputed"] = False
    df["Closed_Imputed"] = False
    df["Competition_Start_Imputed"] = False
    df["Competition_End_Imputed"] = False

    # --- Create masks before imputation ---
    opened_from_start_mask = df["Opened"].isna() & df["Competition_Start"].notna()
    closed_from_end_mask = df["Closed"].isna() & df["Competition_End"].notna()
    start_from_opened_mask = df["Competition_Start"].isna() & df["Opened"].notna()
    end_from_closed_mask = df["Competition_End"].isna() & df["Closed"].notna()

    # --- Apply imputations ---
    df.loc[start_from_opened_mask, "Competition_Start"] = df.loc[start_from_opened_mask, "Opened"]
    df.loc[end_from_closed_mask, "Competition_End"] = df.loc[end_from_closed_mask, "Closed"]
    df.loc[opened_from_start_mask, "Opened"] = df.loc[opened_from_start_mask, "Competition_Start"]
    df.loc[closed_from_end_mask, "Closed"] = df.loc[closed_from_end_mask, "Competition_End"]

    # --- Set flags where imputations occurred ---
    df.loc[opened_from_start_mask, "Opened_Imputed"] = True
    df.loc[closed_from_end_mask, "Closed_Imputed"] = True
    df.loc[start_from_opened_mask, "Competition_Start_Imputed"] = True
    df.loc[end_from_closed_mask, "Competition_End_Imputed"] = True

    return df

In [ ]:
editions_df = impute_games_and_competition_dates(editions_df)

In [ ]:
df_nan_percentage(editions_df)


In [ ]:
editions_df['Edition_Name'].unique()
# Game_Type Edition_Name


In [ ]:
game_types_list= ['Olympic Games', 'Intercalated Games', 'Youth Olympic Games','Forerunners to the Olympic Games']
edition_names_list=['Summer', 'Winter', 'Equestrian']


no_duplicate_games_check = pa.Check(
    lambda df: not df.duplicated(subset=["Year", "Edition_Name", "Game_Type"]).any(),
    element_wise=False,
    error="Duplicate game editions detected based on Year, Edition_Name, and Game_Type."
)

edition_date_check = pa.Check(
    lambda df: (
        # Opened <= Closed  (or either missing)
        (df["Opened"].isna() | df["Closed"].isna() | (df["Opened"] <= df["Closed"]))
    ).all(),
    element_wise=False,
    error="Chronological order violated: check Opened, Closed edition dates."
)

Competition_date_check = pa.Check(
    lambda df: (

        # Competition_Start <= Competition_End  (or either missing)
        (df["Competition_Start"].isna() | df["Competition_End"].isna() | (df["Competition_Start"] <= df["Competition_End"]))
        
    ).all(),
    element_wise=False,
    error="Chronological order violated:check Start, End Competition dates."
)

edition_Competition_date_check = pa.Check(
    lambda df: (

        # Opened <= Competition_Start  (or either missing)
        (df["Opened"].isna() | df["Competition_Start"].isna() | (df["Opened"] <= df["Competition_Start"]))
    ).all(),
    element_wise=False,
    error="Chronological order violated: check Opened, Competition Start dates."
)


# --- Schema Definition ---
games_schema = pa.DataFrameSchema(
    {   
        # id
        "Year": pa.Column(int, pa.Check.between(1850, 2024), nullable=False),
        "Game_Type": pa.Column(str,pa.Check.isin(game_types_list), nullable=False),
        "Edition_Name": pa.Column(str,pa.Check.isin(edition_names_list), nullable=True),

        "City": pa.Column(str, nullable=False),
        "Country": pa.Column(str, nullable=False),

        "Opened": pa.Column("datetime64[ns]", nullable=True),
        "Closed": pa.Column("datetime64[ns]", nullable=True),

        "Competition_Start": pa.Column("datetime64[ns]", nullable=True),
        "Competition_End": pa.Column("datetime64[ns]", nullable=True),

        "Comments": pa.Column(str, nullable=True),

    },
    strict=True,
    coerce=True,
    checks=[
        no_duplicate_games_check,
        edition_date_check,
        Competition_date_check,
        edition_Competition_date_check      # ensure chronological order

    ],
    name="games_schema"
)

# --- Validation Example ---
try:
    games_schema.validate(editions_df, lazy=True)
    print("Validation PASSED!")
except pa.errors.SchemaErrors as exc:
    print("Validation FAILED!")
    error_df = exc.failure_cases
    print(exc)


In [ ]:
dim_affiliation_df

In [ ]:
def rename_df_columns(df, names_dict):
    df = df.copy()
    df = df.rename(columns= names_dict)
    return df

In [ ]:
events_fact_table_columns_names =\
{
    "Athlete_Id": "athlete_id",
    "As": "dim_as",
    "NOC": "dim_noc",
    "Discipline": "dim_discipline",
    "Game Type": "dim_game_type",
    "Game Year": "dim_game_year",
    "Event": "d_event_name",
    "Team": "d_team_name",
    "Tied": "m_tied_flag",
    "Position":"m_position",
    "Medal":"m_medal"

}

athlete_dim_table_columns_names =\
{
    "Athlete_Id": "athlete_id",
    "Roles": "athlete_roles",
    "Sex": "athlete_sex",
    "NOC": "athlete_NOC",
    "Name": "athlete_name",
    "Height (cm)": "athlete_height_cm",
    "Weight (kg)": "athlete_weight_kg",
    "Born_Date": "athlete_born_date",
    "Died_Date":"athlete_died_date",
    "Is_Alive":"athlete_is_alive",
    "Born_City":"athlete_born_city",
    "Born_Region":"athlete_born_region",
    "Born_Country":"athlete_born_country",
    "Height_Imputed":"athlete_is_height_imputed",
    "Weight_Imputed":"athlete_is_weight_imputed",
    "Born_Country_From_NOC":"athlete_is_born_country_from_NOC"

}

In [ ]:
rename_df_columns(results_df, events_fact_table_columns_names)

In [ ]:

rename_df_columns(bios_df, athlete_dim_table_columns_names)